In [52]:
# import re
import csv
import sqlite3
import functions
import pandas as pd
import requests as rq
from config import api_key
from textblob import TextBlob
# pip install geopy
from geopy.geocoders import Nominatim
import matplotlib.pyplot as plt
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
#import keras_tuner as kt
from tensorflow import keras
from tensorflow.keras import layers
import pickle

In [4]:
df = pd.read_csv('Resources/airlines_reviews.csv')
df.head(2)

Title              Name Review Date  \
0                    Flight was amazing  Alison Soetantyo  2024-03-01   
1  seats on this aircraft are dreadful      Robert Watson  2024-02-21   

              Airline Verified  \
0  Singapore Airlines     True   
1  Singapore Airlines     True   

                                             Reviews Type of Traveller  \
0    Flight was amazing. The crew onboard this fl...      Solo Leisure   
1    Booking an emergency exit seat still meant h...      Solo Leisure   

     Month Flown                 Route           Class  Seat Comfort  \
0  December 2023  Jakarta to Singapore  Business Class             4   
1  February 2024   Phuket to Singapore   Economy Class             5   

   Staff Service  Food & Beverages  Inflight Entertainment  Value For Money  \
0              4                 4                       4                4   
1              3                 4                       4                1   

   Overall Rating Recommended  
0               9         yes  
1               3          no

In [5]:
conn = sqlite3.connect('airline_passenger_satisfaction.sqlite')
df.to_sql('airlines_reviews', conn, if_exists='replace')
db = conn.cursor()
db.execute('SELECT * FROM airlines_reviews').fetchall()

[(0,
  'Flight was amazing',
  'Alison Soetantyo',
  '2024-03-01',
  'Singapore Airlines',
  'True',
  '  Flight was amazing. The crew onboard this flight were very welcoming, and gave a good atmosphere. The crew serving my aisle goes by the initial “G”. She was very kind & helpful. Gave my mom a bday cake for a late celebration even though it was just a 1hr 45min flight. Seat is well sanitized, legroom is spacious. IFE onboard has many variety of shows, music, etc. Bathroom always kept clean by crew at all times. & Food was delicious, overall this flight is a 9/10',
  'Solo Leisure',
  'December 2023',
  'Jakarta to Singapore',
  'Business Class',
  4,
  4,
  4,
  4,
  4,
  9,
  'yes'),
 (1,
  'seats on this aircraft are dreadful ',
  'Robert Watson',
  '2024-02-21',
  'Singapore Airlines',
  'True',
  '\xa0\xa0Booking an emergency exit seat still meant huge discomfort in a seat far too narrow and poor padding meaning back ache in 90 minute flight. The seats on this aircraft are dread

In [6]:
df = functions.column_work(df)

In [7]:
functions.blob_function(df)

Comment:   Flight was amazing. The crew onboard this flight were very welcoming, and gave a good atmosphere. The crew serving my aisle goes by the initial “G”. She was very kind & helpful. Gave my mom a bday cake for a late celebration even though it was just a 1hr 45min flight. Seat is well sanitized, legroom is spacious. IFE onboard has many variety of shows, music, etc. Bathroom always kept clean by crew at all times. & Food was delicious, overall this flight is a 9/10
Polarity: 0.3846666666666667
Subjectivity: 0.5599999999999999

Comment:   Booking an emergency exit seat still meant huge discomfort in a seat far too narrow and poor padding meaning back ache in 90 minute flight. The seats on this aircraft are dreadful. The headphones and sound on the entertainment system was dreadful.
Polarity: -0.21249999999999997
Subjectivity: 0.6625

Comment:   Excellent performance on all fronts. I would definitely choose to use this airline again. The aircraft is well-maintained and the staff w

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Comment:   Flew Hong Kong to Vancouver. I am a big fan of Cathay Pacific and have retained loyalty over many years now. They have never let me down and I am confident they will always be as supportive as possible in the event of travel difficulties. I no longer live in Asia so opportunities to fly with them are limited. I now will drive 150+ miles across the US/CAN border specifically to fly with them. The only thing I can find fault with is the food service which is perhaps the biggest disappointment and certainly could be stepped up a notch to give a top rated PE experience. This return flight was very full. We left the gate a few minutes late but arrived on time. Despite it being full, the PE cabin was served with the usual efficiency and professionalism of CX. The only downside to the 4.20pm flight is the absence of a dedicated toilet for the PE cabin but otherwise a great flight which was enjoyable and passed quickly and comfortably. Arrived in to YVR in good shape which I feel ju

Title             Airline  \
0                       Flight was amazing  Singapore Airlines   
1     seats on this aircraft are dreadful   Singapore Airlines   
2             Food was plentiful and tasty  Singapore Airlines   
3             “how much food was available  Singapore Airlines   
4          “service was consistently good”  Singapore Airlines   
...                                    ...                 ...   
8095                  an uneventful flight          Korean Air   
8096           Korean Air always impresses          Korean Air   
8097                 didn’t offer anything          Korean Air   
8098       appreciated the service onboard          Korean Air   
8099              genuinely friendly staff          Korean Air   

                                                Reviews Type of Traveller  \
0       Flight was amazing. The crew onboard this fl...      Solo Leisure   
1       Booking an emergency exit seat still meant h...      Solo Leisure   
2       Excellent performance on all fronts. I would...    Family Leisure   
3      Pretty comfortable flight considering I was f...      Solo Leisure   
4      The service was consistently good from start ...    Family Leisure   
...                                                 ...               ...   
8095    KE124, Brisbane to Incheon (A330) and KE867,...          Business   
8096    Our recent flight was our fourth trip to the...    Couple Leisure   
8097    I flew Korean Air from Bali to Seoul in Pres...          Business   
8098    Seoul to Paris with Korean Air. I am traveli...          Business   
8099    The 13 hour flight in Business class from Se...          Business   

      Month Flown                         Route           Class  Seat Comfort  \
0              12          Jakarta to Singapore  Business Class             4   
1               2           Phuket to Singapore   Economy Class             5   
2               2        Siem Reap to Singapore   Economy Class             1   
3               2  Singapore to London Heathrow   Economy Class             5   
4               2       Singapore to Phnom Penh   Economy Class             5   
...           ...                           ...             ...           ...   
8095            6            BNE to ULN via ICN   Economy Class             5   
8096            6            SYD to LHR via ICN   Economy Class             3   
8097            4                    DPS to ICN  Business Class             4   
8098            4                    ICN to CDG  Business Class             5   
8099            4                    ICN to YYZ  Business Class             3   

      Staff Service  Food & Beverages  Inflight Entertainment  \
0                 4                 4                       4   
1                 3                 4                       4   
2                 5                 2                       1   
3                 5                 5                       5   
4                 5                 5                       5   
...             ...               ...                     ...   
8095              4                 5                       3   
8096              5                 5                       4   
8097              5                 5                       5   
8098              1                 3                       4   
8099              5                 3                       3   

      Value For Money  Overall Rating Recommended Year Flown  Polarity  \
0                   4               9         yes       2023  0.384667   
1                   1               3          no       2024 -0.212500   
2                   5              10         yes       2024  0.500000   
3                   5              10         yes       2024  0.325496   
4                   5              10         yes       2024  0.412500   
...               ...             ...         ...        ...       ...   
8095                4               7         y

In [9]:
functions.split_to_via(df)

Title             Airline  \
0                       Flight was amazing  Singapore Airlines   
1     seats on this aircraft are dreadful   Singapore Airlines   
2             Food was plentiful and tasty  Singapore Airlines   
3             “how much food was available  Singapore Airlines   
4          “service was consistently good”  Singapore Airlines   
...                                    ...                 ...   
8095                  an uneventful flight          Korean Air   
8096           Korean Air always impresses          Korean Air   
8097                 didn’t offer anything          Korean Air   
8098       appreciated the service onboard          Korean Air   
8099              genuinely friendly staff          Korean Air   

                                                Reviews Type of Traveller  \
0       Flight was amazing. The crew onboard this fl...      Solo Leisure   
1       Booking an emergency exit seat still meant h...      Solo Leisure   
2       Excellent performance on all fronts. I would...    Family Leisure   
3      Pretty comfortable flight considering I was f...      Solo Leisure   
4      The service was consistently good from start ...    Family Leisure   
...                                                 ...               ...   
8095    KE124, Brisbane to Incheon (A330) and KE867,...          Business   
8096    Our recent flight was our fourth trip to the...    Couple Leisure   
8097    I flew Korean Air from Bali to Seoul in Pres...          Business   
8098    Seoul to Paris with Korean Air. I am traveli...          Business   
8099    The 13 hour flight in Business class from Se...          Business   

      Month Flown                         Route           Class  Seat Comfort  \
0              12          Jakarta to Singapore  Business Class             4   
1               2           Phuket to Singapore   Economy Class             5   
2               2        Siem Reap to Singapore   Economy Class             1   
3               2  Singapore to London Heathrow   Economy Class             5   
4               2       Singapore to Phnom Penh   Economy Class             5   
...           ...                           ...             ...           ...   
8095            6            BNE to ULN via ICN   Economy Class             5   
8096            6            SYD to LHR via ICN   Economy Class             3   
8097            4                    DPS to ICN  Business Class             4   
8098            4                    ICN to CDG  Business Class             5   
8099            4                    ICN to YYZ  Business Class             3   

      Staff Service  Food & Beverages  Inflight Entertainment  \
0                 4                 4                       4   
1                 3                 4                       4   
2                 5                 2                       1   
3                 5                 5                       5   
4                 5                 5                       5   
...             ...               ...                     ...   
8095              4                 5                       3   
8096              5                 5                       4   
8097              5                 5                       5   
8098              1                 3                       4   
8099              5                 3                       3   

      Value For Money  Overall Rating Recommended Year Flown  Polarity  \
0                   4               9         yes       2023  0.384667   
1                   1               3          no       2024 -0.212500   
2                   5              10         yes       2024  0.500000   
3                   5              10         yes       2024  0.325496   
4                   5              10         yes       2024  0.412500   
...               ...             ...         ...        ...       ...   
8095                4               7         y

In [10]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (8100, 20)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via'],
      dtype='object')

In [11]:
airport_codes = pd.read_csv('Resources/airports_utf.csv')

In [12]:
unique_origins = df['Origin'].unique()
airports_origins = airport_codes['City'].tolist() + airport_codes['Code'].tolist()
origins_values_not_found = [origin for origin in unique_origins if origin not in airports_origins]

print("Values from the 'Origin' column not found in airports_utf.csv 'City' or 'Code' columns:")
print(origins_values_not_found)

Values from the 'Origin' column not found in airports_utf.csv 'City' or 'Code' columns:
['Spain', 'Hyderabad', 'USA', 'United States', 'Mexico', 'Santiago', 'Panama', 'China', 'New Yok', 'Canada', 'Malaysia', 'India', 'Panama City', 'Turkey', 'Was', 'IA', 'New U=York', 'San José', 'Geneva and Paris CDG']


In [13]:
### NEEDS FX !!!!!!!!!!!!!!!!!!!!!!!!!!

values_to_exclude_origin = ['Spain', 'Hyderabad', 'USA', 'United States', 'Mexico', 'Santiago', 'Panama',
    'China', 'New Yok', 'Canada', 'Malaysia', 'India', 'Panama City', 'Turkey', 'Was', 'IA',
    'New U=York', 'San José', 'Geneva and Paris CDG']

# Keep only rows where 'Origin' column values are not in the list of values to exclude
df = df[~df['Origin'].isin(values_to_exclude_origin)]

In [14]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (8064, 20)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via'],
      dtype='object')

In [15]:
unique_destinations = df['Destination'].unique()
airports_destinations = airport_codes['City'].tolist() + airport_codes['Code'].tolist()
destinations_values_not_found = [destination for destination in unique_destinations if destination not in airports_destinations]

print("Values from the 'Destination' column not found in airports_utf.csv 'City' or 'Code' columns:")
print(destinations_values_not_found)

Values from the 'Destination' column not found in airports_utf.csv 'City' or 'Code' columns:
['', 'Hyderabad', 'Lahore VIA \\DOHA', 'Japan', 'Hydrabad', 'Arla', 'Panama City', 'Panama', 'Panamá', 'New York City', 'Panamá City', 'Hing Kong', 'Los  Angeles', 'new York', 'Auckland and return', 'Hong kong', 'Taiwan', 'Korea', '- New York']


In [16]:
### NEEDS FX !!!!!!!!!!!!!!!!!!!!!!!!!!
values_to_exclude_destination = ['', 'Hyderabad', 'Lahore VIA \\DOHA', 'Japan', 'Hydrabad', 'Arla',
                                 'Panama City', 'Turkey', 'Panama', 'Panamá', 'Colombia', 'New York City',
                                 'Panamá City', None, 'Hing Kong', 'new York', 'Auckland and return',
                                 'Hong kong', 'Taiwan', 'Korea', '- New York']

# Keep only rows where 'Destination' column values are not in the list of values to exclude
df = df[~df['Destination'].isin(values_to_exclude_destination)]

In [17]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (8027, 20)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via'],
      dtype='object')

In [18]:
unique_via = df['Via'].unique()
airports_via = airport_codes['City'].tolist() + airport_codes['Code'].tolist()
via_values_not_found = [via for via in unique_via if via not in airports_via]

print("Values from the 'Via' column not found in airports_utf.csv 'City' or 'Code' columns:")
print(via_values_not_found)

Values from the 'Via' column not found in airports_utf.csv 'City' or 'Code' columns:
[None, 'Hong', 'New', 'DOA', 'Lagoa', 'DXBMLE', 'Los', 'Kuala', 'Минск', 'San', 'São', 'Panama', nan, 'Sao', 'paris', 'Italy', 'Washington,', 'Lyons', 'Hongkong', 'Ho', 'Degeau', 'INC']


In [15]:
# from functions import split_via_2

In [16]:
# df = df.apply(split_via_2, axis=1)

In [19]:
values_to_exclude_via = ['Hong', 'New', 'DOA', 'Lagoa', 'DXBMLE', 'Los', 'Kuala', 'Минск',
                         'San', 'São', 'Panama', 'Sao', 'paris', 'Italy', 'Washington,',
                         'Lyons', 'Hongkong', 'Ho', 'Degeau', 'INC']

# Keep only rows where 'Via' column values are not in the list of values to exclude
df = df[~df['Via'].isin(values_to_exclude_via)]

In [21]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (7750, 20)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via'],
      dtype='object')

In [20]:
# unique_via_2 = df['Via'].unique()
# airports_via_2 = airport_codes['City'].tolist() + airport_codes['Code'].tolist()
# via_2_values_not_found = [via_2 for via_2 in unique_via_2 if via_2 not in airports_via_2]

# print("Values from the 'Via_2' column not found in airports_utf.csv 'City' or 'Code' columns:")
# print(via_2_values_not_found)

Values from the 'Via_2' column not found in airports_utf.csv 'City' or 'Code' columns:
[None, '']


In [22]:
df['Via'].value_counts()

Via
Doha         951
Istanbul     855
Dubai        618
Paris        275
Singapore    263
            ... 
Dhaka          1
Seattle        1
Oslo           1
Harare         1
SYD            1
Name: count, Length: 119, dtype: int64

In [24]:
# df['Via_2'].value_counts()

In [25]:
# df['Origin'].apply(functions.lookup_code)

In [26]:
# df['Origin'].apply(functions.lookup_city)

In [27]:
df['Origin']

0         Jakarta
1          Phuket
2       Siem Reap
3       Singapore
4       Singapore
          ...    
8095          BNE
8096          SYD
8097          DPS
8098          ICN
8099          ICN
Name: Origin, Length: 7750, dtype: object

In [28]:
### Calling Existing FX !!!!!!!!!!!!!!!!!!!!!!!!!!

from functions import find_airport_code

In [30]:
### NEEDS FX !!!!!!!!!!!!!!!!!!!!!!!!!!

df['Origin_Code'] = df['Origin'].apply(lambda x: find_airport_code(x, airport_codes))
df['Destination_Code'] = df['Destination'].apply(lambda x: find_airport_code(x, airport_codes))
df['Via_Code'] = df['Via'].apply(lambda x: find_airport_code(x, airport_codes))
# df['Via_2_Code'] = df['Via_2'].apply(lambda x: find_airport_code(x, airport_codes))

In [31]:
df.columns

Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via', 'Origin_Code', 'Destination_Code', 'Via_Code'],
      dtype='object')

In [32]:
df['Origin_Code']

0       CGK
1       HKT
2       SAI
3       SIN
4       SIN
       ... 
8095    BNE
8096    SYD
8097    DPS
8098    ICN
8099    ICN
Name: Origin_Code, Length: 7750, dtype: object

In [33]:
df['Destination_Code']

0       SIN
1       SIN
2       SIN
3       LHR
4       PNH
       ... 
8095    ULN
8096    LHR
8097    ICN
8098    CDG
8099    YYZ
Name: Destination_Code, Length: 7750, dtype: object

In [34]:
df['Via_Code']

0       None
1       None
2       None
3       None
4       None
        ... 
8095     ICN
8096     ICN
8097    None
8098    None
8099    None
Name: Via_Code, Length: 7750, dtype: object

In [35]:
# df['Via_2_Code']

In [36]:
### Calling Existing FX !!!!!!!!!!!!!!!!!!!!!!!!!!

from functions import find_airport_city

In [37]:
### NEEDS FX !!!!!!!!!!!!!!!!!!!!!!!!!!

df['Origin_City'] = df['Origin'].apply(lambda x: find_airport_city(x, airport_codes))
df['Destination_City'] = df['Destination'].apply(lambda x: find_airport_city(x, airport_codes))
df['Via_City'] = df['Via'].apply(lambda x: find_airport_city(x, airport_codes))
# df['Via_2_City'] = df['Via_2'].apply(lambda x: find_airport_city(x, airport_codes))   

In [38]:
df.columns

Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via', 'Origin_Code', 'Destination_Code', 'Via_Code',
       'Origin_City', 'Destination_City', 'Via_City'],
      dtype='object')

In [39]:
df['Origin_City']

0                              Jakarta
1                               Phuket
2                            Siem Reap
3                            Singapore
4                            Singapore
                     ...              
8095                         Brisibane
8096                            sydney
8097                     Denpasar Bali
8098    Incheon, Incheon Int'l Airport
8099    Incheon, Incheon Int'l Airport
Name: Origin_City, Length: 7750, dtype: object

In [40]:
df['Destination_City']

0                            Singapore
1                            Singapore
2                            Singapore
3                      London Heathrow
4                           Phnom Penh
                     ...              
8095                       Ulaanbaatar
8096                          Heathrow
8097    Incheon, Incheon Int'l Airport
8098                         Paris cdg
8099       Toronto - Lester B. Pearson
Name: Destination_City, Length: 7750, dtype: object

In [41]:
df['Via_City']

0                                 None
1                                 None
2                                 None
3                                 None
4                                 None
                     ...              
8095    Incheon, Incheon Int'l Airport
8096    Incheon, Incheon Int'l Airport
8097                              None
8098                              None
8099                              None
Name: Via_City, Length: 7750, dtype: object

In [39]:
# df['Via_2_City']

0        NaN
1        NaN
2        NaN
3        NaN
4        NaN
        ... 
8095    None
8096    None
8097     NaN
8098     NaN
8099     NaN
Name: Via_2_City, Length: 8011, dtype: object

In [42]:
df.head()

Title             Airline  \
0                    Flight was amazing  Singapore Airlines   
1  seats on this aircraft are dreadful   Singapore Airlines   
2          Food was plentiful and tasty  Singapore Airlines   
3          “how much food was available  Singapore Airlines   
4       “service was consistently good”  Singapore Airlines   

                                             Reviews Type of Traveller  \
0    Flight was amazing. The crew onboard this fl...      Solo Leisure   
1    Booking an emergency exit seat still meant h...      Solo Leisure   
2    Excellent performance on all fronts. I would...    Family Leisure   
3   Pretty comfortable flight considering I was f...      Solo Leisure   
4   The service was consistently good from start ...    Family Leisure   

   Month Flown                         Route           Class  Seat Comfort  \
0           12          Jakarta to Singapore  Business Class             4   
1            2           Phuket to Singapore   Economy Class             5   
2            2        Siem Reap to Singapore   Economy Class             1   
3            2  Singapore to London Heathrow   Economy Class             5   
4            2       Singapore to Phnom Penh   Economy Class             5   

   Staff Service  Food & Beverages  ...  Subjectivity     Origin  \
0              4                 4  ...      0.560000    Jakarta   
1              3                 4  ...      0.662500     Phuket   
2              5                 2  ...      0.750000  Siem Reap   
3              5                 5  ...      0.565488  Singapore   
4              5                 5  ...      0.537500  Singapore   

       Destination   Via Origin_Code  Destination_Code  Via_Code Origin_City  \
0        Singapore  None         CGK               SIN      None     Jakarta   
1        Singapore  None         HKT               SIN      None      Phuket   
2        Singapore  None         SAI               SIN      None   Siem Reap   
3  London Heathrow  None         SIN               LHR      None   Singapore   
4       Phnom Penh  None         SIN               PNH      None   Singapore   

  Destination_City Via_City  
0        Singapore     None  
1        Singapore     None  
2        Singapore     None  
3  London Heathrow     None  
4       Phnom Penh     None  

[5 rows x 26 columns]

In [47]:
one_hot_e(df)

Title             Airline  \
0                       Flight was amazing  Singapore Airlines   
1     seats on this aircraft are dreadful   Singapore Airlines   
2             Food was plentiful and tasty  Singapore Airlines   
3             “how much food was available  Singapore Airlines   
4          “service was consistently good”  Singapore Airlines   
...                                    ...                 ...   
8095                  an uneventful flight          Korean Air   
8096           Korean Air always impresses          Korean Air   
8097                 didn’t offer anything          Korean Air   
8098       appreciated the service onboard          Korean Air   
8099              genuinely friendly staff          Korean Air   

                                                Reviews  Month Flown  \
0       Flight was amazing. The crew onboard this fl...           12   
1       Booking an emergency exit seat still meant h...            2   
2       Excellent performance on all fronts. I would...            2   
3      Pretty comfortable flight considering I was f...            2   
4      The service was consistently good from start ...            2   
...                                                 ...          ...   
8095    KE124, Brisbane to Incheon (A330) and KE867,...            6   
8096    Our recent flight was our fourth trip to the...            6   
8097    I flew Korean Air from Bali to Seoul in Pres...            4   
8098    Seoul to Paris with Korean Air. I am traveli...            4   
8099    The 13 hour flight in Business class from Se...            4   

                             Route  Seat Comfort  Staff Service  \
0             Jakarta to Singapore             4              4   
1              Phuket to Singapore             5              3   
2           Siem Reap to Singapore             1              5   
3     Singapore to London Heathrow             5              5   
4          Singapore to Phnom Penh             5              5   
...                            ...           ...            ...   
8095            BNE to ULN via ICN             5              4   
8096            SYD to LHR via ICN             3              5   
8097                    DPS to ICN             4              5   
8098                    ICN to CDG             5              1   
8099                    ICN to YYZ             3              5   

      Food & Beverages  Inflight Entertainment  Value For Money  ...  \
0                    4                       4                4  ...   
1                    4                       4                1  ...   
2                    2                       1                5  ...   
3                    5                       5                5  ...   
4                    5                       5                5  ...   
...                ...                     ...              ...  ...   
8095                 5                       3                4  ...   
8096                 5                       4                5  ...   
8097                 5                       5                1  ...   
8098                 3                       4                5  ...   
8099                 3                       3                5  ...   

                    Destination_City                        Via_City  \
0                          Singapore                            None   
1                          Singapore                            None   
2                          Singapore                            None   
3                    London Heathrow                            None   
4                         Phnom Penh                            None   
...                              ...                             ...   
8095                     Ulaanbaatar  Incheon, Incheon Int'l Airport   
8096                        Heathrow  Incheon, Incheon Int'l Airport   
8097  Incheon, Incheon Int'l Airport                         

In [48]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (7750, 26)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via', 'Origin_Code', 'Destination_Code', 'Via_Code',
       'Origin_City', 'Destination_City', 'Via_City'],
      dtype='object')

In [49]:
def col_work_dos(df):

    #Keep certain columns
    

    df = df[[ 'Airline', 'Month Flown', 'Year Flown', 'Seat Comfort',
       'Staff Service', 'Food & Beverages', 'Inflight Entertainment',
       'Value For Money', 'Overall Rating', 'Recommended',
       'Origin', 'Origin_Code', 'Origin_City', 'Destination', 'Destination_Code', 'Destination_City',
       'Via', 'Via_Code', 'Via_City', 'Comment Polarity', 'Comment Subjectivity',
        'Title Polarity', 'Title Subjectivity', 'Class_Business Class', 'Class_Economy Class', 'Class_First Class',
       'Class_Premium Economy', 'Type of Traveller_Business',
       'Type of Traveller_Couple Leisure', 'Type of Traveller_Family Leisure',
       'Type of Traveller_Solo Leisure']]
    
    
    # reformat recommended column values
    df['Recommended'] = df['Recommended'].replace({'no':0, 'yes':1})

    return df

In [50]:
print(f'Rows and Columns: {df.shape}')
df.columns

Rows and Columns: (7750, 26)


Index(['Title', 'Airline', 'Reviews', 'Type of Traveller', 'Month Flown',
       'Route', 'Class', 'Seat Comfort', 'Staff Service', 'Food & Beverages',
       'Inflight Entertainment', 'Value For Money', 'Overall Rating',
       'Recommended', 'Year Flown', 'Polarity', 'Subjectivity', 'Origin',
       'Destination', 'Via', 'Origin_Code', 'Destination_Code', 'Via_Code',
       'Origin_City', 'Destination_City', 'Via_City'],
      dtype='object')

In [53]:
pickle.dump(df, open('df.pkl','wb'))

In [41]:
custom_user_agent = "MyCustomUserAgent"
geolocator = Nominatim(user_agent="custom_user_agent")

In [45]:
def get_lat_long(airport_code):
    geolocator = Nominatim(user_agent="custom_user_agent")
    location = geolocator.geocode(airport_code)
    if location:
        return location.latitude, location.longitude
    else:
        return None, None

# Apply the function to create new columns for Origin_Latitude, Origin_Longitude, Destination_Latitude, Destination_Longitude for the first 10 rows
df_subset = df.head(10)
df_subset['Origin_Latitude'], df_subset['Origin_Longitude'] = zip(*df_subset['Origin_Code'].apply(get_lat_long))
df_subset['Destination_Latitude'], df_subset['Destination_Longitude'] = zip(*df_subset['Destination_Code'].apply(get_lat_long))

# Display the updated DataFrame for the first 10 rows
print(df_subset)

              Airline           Class          Destination  Food & Beverages  \
0  Singapore Airlines  Business Class            Singapore                 4   
1  Singapore Airlines   Economy Class            Singapore                 4   
2  Singapore Airlines   Economy Class            Singapore                 2   
3  Singapore Airlines   Economy Class      London Heathrow                 5   
4  Singapore Airlines   Economy Class           Phnom Penh                 5   
5  Singapore Airlines   Economy Class               Cairns                 5   
6  Singapore Airlines   Economy Class            Frankfurt                 1   
7  Singapore Airlines   Economy Class  Bandar Seri Begawan                 3   
8  Singapore Airlines   Economy Class              Jakarta                 5   
9  Singapore Airlines   Economy Class            Singapore                 4   

   Inflight Entertainment  Month Flown     Origin  Overall Rating  Polarity  \
0                       4           12  

In [47]:
df.head()

Airline           Class      Destination  Food & Beverages  \
0  Singapore Airlines  Business Class        Singapore                 4   
1  Singapore Airlines   Economy Class        Singapore                 4   
2  Singapore Airlines   Economy Class        Singapore                 2   
3  Singapore Airlines   Economy Class  London Heathrow                 5   
4  Singapore Airlines   Economy Class       Phnom Penh                 5   

   Inflight Entertainment  Month Flown     Origin  Overall Rating  Polarity  \
0                       4           12    Jakarta               9  0.384667   
1                       4            2     Phuket               3 -0.212500   
2                       1            2  Siem Reap              10  0.500000   
3                       5            2  Singapore              10  0.325496   
4                       5            2  Singapore              10  0.412500   

  Recommended  ... Via_2 Year Flown  Origin_Code  Destination_Code  Via_Code  \
0         yes  ...   NaN       2023          CGK               SIN      None   
1          no  ...   NaN       2024          HKT               SIN      None   
2         yes  ...   NaN       2024          SAI               SIN      None   
3         yes  ...   NaN       2024          SIN               LHR      None   
4         yes  ...   NaN       2024          SIN               PNH      None   

  Via_2_Code Origin_City  Destination_City Via_City Via_2_City  
0        NaN     Jakarta         Singapore     None        NaN  
1        NaN      Phuket         Singapore     None        NaN  
2        NaN   Siem Reap         Singapore     None        NaN  
3        NaN   Singapore   London Heathrow     None        NaN  
4        NaN   Singapore        Phnom Penh     None        NaN  

[5 rows x 29 columns]

In [49]:
len(unique_Origin)

654

In [ ]:
print(df['Origin_Code'].dtype)
print(df['Destination_Code'].dtype)
print(df['Via_Code'].dtype)
print(df['Via_2_Code'].dtype)

In [ ]:
df['Origin_Code'] = df['Origin_Code'].astype('category')
df['Destination_Code'] = df['Destination_Code'].astype('category')
df['Via_Code'] = df['Via_Code'].astype('category')
df['Via_2_Code'] = df['Via_2_Code'].astype('category')

In [ ]:
print(df['Origin_Code'].dtype)
print(df['Destination_Code'].dtype)
print(df['Via_Code'].dtype)
print(df['Via_2_Code'].dtype)

consider optimizing your code further by looking into other ways to improve the efficiency of your operations, such as using vectorized operations, avoiding unnecessary iterations, and utilizing appropriate indexing techniques

Avoid unnecessary iterations
1. **Use Vectorized Operations**: Instead of iterating over rows, try to perform operations on entire columns or subsets of data using vectorized operations provided by libraries like NumPy and Pandas. These operations are optimized for performance and can significantly speed up your code.

2. **Avoid Iterating Over DataFrame Rows**: If possible, avoid iterating over rows using methods like `iterrows()` or `apply()`. These methods can be slow, especially on large datasets. Instead, try to find ways to apply operations to entire columns or use built-in Pandas functions that operate on the entire DataFrame.

3. **Use GroupBy**: If you need to perform operations on groups of data, consider using the `groupby()` function in Pandas. This allows you to group your data based on certain criteria and apply functions to each group without explicit iteration.

4. **Merge and Join Operations**: Instead of iterating over two DataFrames to perform operations, consider using merge and join operations provided by Pandas. These operations are optimized and can be more efficient than iterating over rows.

5. **List Comprehensions and Built-in Functions**: When possible, use list comprehensions or built-in functions to perform operations on lists or arrays. These are typically faster than explicit loops and can make your code more concise and readable.

6. **Utilize NumPy Functions**: NumPy provides a wide range of vectorized functions that can operate on arrays efficiently. Wherever possible, try to use NumPy functions instead of writing custom Python loops.

By following these tips and leveraging the capabilities of libraries like Pandas and NumPy, you can avoid unnecessary iterations and improve the performance of your code

In [ ]:
# Convert the column back to its original data type
df['Origin_Code'] = df['Origin_Code'].astype('original_data_type')
df['Destination_Code'] = df['Destination_Code'].astype('original_data_type')
df['Via_Code'] = df['Via_Code'].astype('original_data_type')
df['Via_2_Code'] = df['Via_2_Code'].astype('original_data_type')
print(df['Origin_Code'].dtype)

https://www.developer.aero/api-catalog/flight-duration-overview

In [17]:
####### DO NOT RUN !!!!!!!!!!
# unique_via = df['Via'].unique()
# airports_via = airport_codes['City'].tolist() + airport_codes['Code'].tolist()
# via_values_not_found = [via for via in unique_via if via not in airports_via]

# print("Values from the 'Via' column not found in airports_utf.csv 'City' or 'Code' columns:")
# print(via_values_not_found)

# Values from the 'Via' column not found in airports_utf.csv 'City' or 'Code' columns:
# [None, 'DOA', 'Lagoa', 'DXB/MLE', 'Минск', 'Panama city', '', 'paris', 'Italy', 'Lyons', 'Hongkong', 'Hong kong', 'Degeau', 'INC']

Values from the 'Via' column not found in airports_utf.csv 'City' or 'Code' columns:
[None, 'DOA', 'Lagoa', 'DXB/MLE', 'Минск', 'Panama city', '', 'paris', 'Italy', 'Lyons', 'Hongkong', 'Hong kong', 'Degeau', 'INC']


In [ ]:
### lookup failures, only return cities not found, if return series call unique.apply - return nothing if you can't find it

### get lats/long for origin-destination-via

### https://www.developer.aero/api-catalog/flight-duration-overview

In [ ]:
# keep routes & split into Origin & Destination, find coord for the locations
# Target "Recommended"
# maybe user can provide the following and 
# Type of Traveller', 'Route', 'Class', 'Seat Comfort',
# 'Staff Service', 'Food & Beverages', 'Inflight Entertainment',
# 'Value For Money